# Note
Your docker-compose.yaml exposes Kafka on two ports:
- Internal port 9092 (for container-to-container communication)
- External port 29092 (for host-to-container communication)


In [1]:
from aiokafka import AIOKafkaProducer, AIOKafkaConsumer
from aiokafka.structs import TopicPartition
import asyncio

from typing import Optional
import json

producer = AIOKafkaProducer(bootstrap_servers="localhost:29092", enable_idempotence=True)
consumer = AIOKafkaConsumer(bootstrap_servers="localhost:29092", auto_offset_reset="earliest")
await producer.start()
await consumer.start()

Unable to request metadata from node with id 1: KafkaConnectionError('Connection at localhost:29092 closed')
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 closed
Unable to update metadata from [1]
Unable connect to node with id 1: KafkaConnectionError: Connection at localhost:29092 cl

In [5]:
await producer.send_and_wait("test-topic", b"dkssud", partition=0)

RecordMetadata(topic='test-topic', partition=0, topic_partition=TopicPartition(topic='test-topic', partition=0), offset=2, timestamp=1746604028443, timestamp_type=0, log_start_offset=0)

In [7]:
# Subscribe to the topic
# await consumer.subscribe(['test-topic'])

# For testing specific partition access, you can use:
partition = TopicPartition('test-topic', 0)  # Accessing partition 0

# Seek to beginning to read older messages
# Wait for partitions to be assigned first
while not consumer.assignment():
    await asyncio.sleep(0.1)

# Seek to beginning of this specific partition
await consumer.seek_to_beginning(partition)

# Now try to get a message
try:
    message = await consumer.getone()
    print(f"Received message: {message.value.decode()}")
except Exception as e:
    print(f"Error getting message: {e}")

Received message: test


In [9]:
await consumer.getone()

ConsumerRecord(topic='test-topic', partition=0, offset=2, timestamp=1746604028443, timestamp_type=0, key=None, value=b'dkssud', checksum=None, serialized_key_size=-1, serialized_value_size=6, headers=())

In [1]:
from typing import TypedDict, Optional


class Knowledge(TypedDict):
    id: str
    user_id: str
    run_id: Optional[str]
    data: str
    metadata: Optional[dict]

In [3]:
from aiokafka import AIOKafkaProducer, AIOKafkaConsumer
from typing import Optional
import json


class KafkaAddQueue:
    def __init__(self, topic: str, producer: Optional[AIOKafkaProducer], consumer: Optional[AIOKafkaConsumer]):
        self.topic = topic
        self.producer = producer
        self.consumer = consumer

    async def put(self, knowledge: Knowledge):
        if self.producer is None:
            raise ValueError("Producer is not initialized")
        input_data = json.dumps(knowledge)
        input_data = input_data.encode("utf-8")
        await self.producer.send_and_wait(self.topic, input_data)

    async def get(self) -> Knowledge:
        if self.consumer is None:
            raise ValueError("Consumer is not initialized")
        return await self.consumer.getone()


In [4]:
producer = AIOKafkaProducer(bootstrap_servers="localhost:29092", enable_idempotence=True)
consumer = AIOKafkaConsumer("test-topic", bootstrap_servers="localhost:29092", auto_offset_reset="earliest", group_id="test-group")
queue = KafkaAddQueue("test-topic",producer, consumer)

In [5]:
await producer.start()

In [6]:

await consumer.start()

Group Coordinator Request failed: [Error 15] GroupCoordinatorNotAvailableError
Marking the coordinator dead (node 1)for group test-group.


In [12]:
await producer.stop()
await consumer.stop()

In [6]:
await queue.put(Knowledge(id="1", user_id="1", data="test", metadata={}))

In [ ]:
await queue.get()

In [1]:
await consumer.stop()

NameError: name 'consumer' is not defined